# On finding the right topologies for a given reaction

[Molecular dimensions of adsorptives](http://pubs.acs.org/doi/abs/10.1021/ja973906m)

In [2]:
import math
import pandas as pd

from bokeh.io import output_notebook
from bokeh.plotting import figure, show, output_file
from bokeh.charts import Bar
from bokeh.charts.attributes import cat
from bokeh.models import HoverTool, ColumnDataSource, FixedTicker
from bokeh.palettes import Category10, Set1, Spectral

output_notebook()

Loading BokehJS ...

In [3]:
def assign_label(rings):
    '''
    assign string labels to a list of ints
    matching the usual zeolite pore size labels
    '''

    if max(rings) == 8:
        return 's'
    elif max(rings) == 10:
        if 8 in rings:
            return 'ms'
        else:
            return 'm'
    elif max(rings) == 12:
        if 10 in rings and 8 in rings:
            return 'lms'
        elif 10 in rings:
            return 'lm'
        elif 8 in rings:
            return 'ls'
        else:
            return 'l'
    elif max(rings) > 12:
        return 'x'
    else:
        return None
    
def are_all_even(lst):
    'check if all the elements of a list are even numbers'

    return all(x % 2 == 0 for x in lst)

In [4]:
from zefram import get_session, get_table, framework, Framework, RingSize

df = get_table('frameworks')

df.loc[:, 'Rings'] = [[r.size for r in framework(row['code']).ring_sizes] for i, row in df.iterrows()]
# get the largest ring
df.loc[:, 'max_ring'] = df['Rings'].apply(max)
# assign a string label
df.loc[:, 'ring_label'] = df.Rings.apply(assign_label)
df.loc[:, 'alpo_possible'] = df.Rings.apply(are_all_even)
df.rename(columns={'lcd': 'Largest cavity dia.', 'pld': 'Pore limiting dia.',
                   'maxdsi': 'Max dia. of inc. sphere'}, inplace=True)

## Select the frameworks based on the ranges of parameters

- pore limiting diameter in the range [3.5, 4.5]
- largest cavity diameter in the range [5.5, 6.5]

In [24]:
criteria = {'Pore limiting dia.': [3.5, 4.5],
            'Largest cavity dia.':  [5.5, 6.5]}

masks = {}
for k, v in criteria.items():
    vmin, vmax = sorted(v)
    masks[k] = (df[k] >= vmin) & (df[k] < vmax)
    
mask = pd.concat(list(masks.values()), axis=1).all(axis=1)
df.loc[mask, ['code', 'Pore limiting dia.','Largest cavity dia.', 'ring_label', 'Rings', 'alpo_possible']]

code  Pore limiting dia.  Largest cavity dia. ring_label  \
8    AFN                 3.7                  5.9          s   
19   APD                 3.8                  5.6          s   
25   ATT                 4.3                  6.1          s   
28   AWO                 4.3                  5.8          s   
34   BOF                 4.3                  6.2          m   
38   BRE                 3.5                  5.9          s   
41   CAS                 3.5                  5.7          s   
42   CDO                 3.9                  6.4          s   
44   CGF                 3.5                  6.4         ms   
55   DFT                 4.3                  5.7          s   
59   EDI                 4.1                  6.4          s   
63   EPI                 4.1                  6.1          s   
74   GIS                 3.9                  5.6          s   
84   IHW                 4.0                  6.2          s   
104  JOZ                 3.9                  5.6          s   
106  JSN                 4.0                  5.8          s   
108  JST                 3.8                  6.0          m   
154  OWE                 4.4                  6.4          s   
158  PHI                 4.3                  6.0          s   
162  PUN                 4.2                  6.2        lms   
192  SIV                 4.4                  6.0          s   
195  SOS                 4.2                  5.5         ls   
203  STW                 4.1                  6.1         ms   
208  THO                 4.1                  5.8          s   
213  UEI                 4.4                  6.2          s   

                 Rings alpo_possible  
8            [8, 6, 4]          True  
19           [8, 6, 4]          True  
25           [8, 6, 4]          True  
28           [8, 6, 4]          True  
34       [10, 6, 5, 4]         False  
38        [8, 6, 5, 4]         False  
41           [8, 6, 5]         False  
42              [8, 5]         False  
44       [10, 8, 6, 4]          True  
55           [8, 6, 4]          True  
59              [8, 4]          True  
63           [8, 5, 4]         False  
74              [8, 4]          True  
84        [8, 6, 5, 4]         False  
104          [8, 4, 3]         False  
106          [8, 6, 4]          True  
108         [10, 6, 3]         False  
154          [8, 6, 4]          True  
158             [8, 4]          True  
162  [12, 10, 8, 4, 3]         False  
192             [8, 4]          True  
195   [12, 8, 6, 4, 3]         False  
203      [10, 8, 5, 4]         False  
208             [8, 4]          True  
213          [8, 6, 4]          True

### tighter criteria

- pore limiting diameter in the range [3.7, 4.3]
- largest cavity diameter in the range [5.7, 6.3]

In [25]:
criteria = {'Pore limiting dia.': [3.7, 4.3],
            'Largest cavity dia.':  [5.7, 6.3]}

masks = {}
for k, v in criteria.items():
    vmin, vmax = sorted(v)
    masks[k] = (df[k] >= vmin) & (df[k] < vmax)
    
mask = pd.concat(list(masks.values()), axis=1).all(axis=1)
df.loc[mask, ['code', 'Pore limiting dia.','Largest cavity dia.', 'ring_label', 'Rings', 'alpo_possible']]

code  Pore limiting dia.  Largest cavity dia. ring_label  \
8    AFN                 3.7                  5.9          s   
63   EPI                 4.1                  6.1          s   
84   IHW                 4.0                  6.2          s   
106  JSN                 4.0                  5.8          s   
108  JST                 3.8                  6.0          m   
162  PUN                 4.2                  6.2        lms   
203  STW                 4.1                  6.1         ms   
208  THO                 4.1                  5.8          s   

                 Rings alpo_possible  
8            [8, 6, 4]          True  
63           [8, 5, 4]         False  
84        [8, 6, 5, 4]         False  
106          [8, 6, 4]          True  
108         [10, 6, 3]         False  
162  [12, 10, 8, 4, 3]         False  
203      [10, 8, 5, 4]         False  
208             [8, 4]          True

### Max diameter of a sphere 

- pore limiting diameter in the range [3.7, 4.3]
- maximum diameter of a sphere that can be included in the range [5.7, 6.3]

In [26]:
criteria = {'Pore limiting dia.': [3.7, 4.3],
            'Max dia. of inc. sphere':  [5.7, 6.3]}

masks = {}
for k, v in criteria.items():
    vmin, vmax = sorted(v)
    masks[k] = (df[k] >= vmin) & (df[k] < vmax)
    
mask = pd.concat(list(masks.values()), axis=1).all(axis=1)
df.loc[mask, ['code', 'Pore limiting dia.', 'Largest cavity dia.',
              'Max dia. of inc. sphere', 'ring_label', 'Rings', 'alpo_possible']]

code  Pore limiting dia.  Largest cavity dia.  Max dia. of inc. sphere  \
42   CDO                 3.9                  6.4                     5.78   
59   EDI                 4.1                  6.4                     5.72   
65   ESV                 3.7                  6.9                     6.22   
153  OSO                 4.2                  6.7                     6.07   
215  UOS                 4.2                  6.5                     5.85   
228  ZON                 4.0                  6.5                     5.83   

    ring_label             Rings alpo_possible  
42           s            [8, 5]         False  
59           s            [8, 4]          True  
65           s      [8, 6, 5, 4]         False  
153          x        [14, 8, 3]         False  
215         ms  [10, 8, 6, 5, 4]         False  
228          s         [8, 6, 4]          True